# Exploring Ticket Sales with Redshift

## Overview

In [1]:
# python imports
import pandas as pd
import numpy as np


## Exploratory Data Analysis

### Tables and Data Structure

### Categories
The `categories` table holds information about different event categories. The attributes captured here are as follows:

- **catid**: unique identifier for each category
- **catgroup**: the group or type the category belongs to (e.g., sports, concerts, theater)
- **catname**: the name of the category (e.g., Baseball, Rock Concert)
- **catdesc**: a description of the category, providing more details about what it encompasses

The `categories` table allows for the analysis of trends in ticket sales in regards to different types of events. Gaining a better understanding of how different event categories perform can help businesses tailor their marketing strategies and inventory management to meet consumer demand more effectively.

In [2]:
select * from public.category

catid  catgroup    catname                                     catdesc
0       2    Sports        NHL                      National Hockey League
1       4    Sports        NBA             National Basketball Association
2       5    Sports        MLS                         Major League Soccer
3       7     Shows      Plays                     All non-musical theatre
4       9  Concerts        Pop             All rock and pop music concerts
5      10  Concerts       Jazz                  All jazz singers and bands
6       1    Sports        MLB                       Major League Baseball
7       3    Sports        NFL                    National Football League
8       6     Shows   Musicals                             Musical theatre
9       8     Shows      Opera                   All opera and light opera
10     11  Concerts  Classical  All symphony, concerto, and choir concerts

The following is a brief overview of the categories dataset, using the `.describe()` method. The output provides us with some key statistics of each column in the dataset, including the mean, max, and min values to understand how data is distributed. This also helps us identify any irregularities or missing values that need to be addressed in the cleaning stage before analysis.

Here are some key points we can infer:

- The `catid` column, being the only numerical data in the `categories` table, is analyzed by the `.describe()` method. It shows the count, mean, standard deviation, minimum, 25th percentile, median (50th percentile), 75th percentile, and maximum values of the category IDs.
- Since `catgroup`, `catname`, and `catdesc` are non-numeric, they are not included in the `.describe()` output. To investigate these columns, we would need to use other methods suitable for textual data analysis.
- The count of `catid` indicates the total number of unique categories present in the dataset.
- The minimum and maximum values of `catid` give us an idea of the range of category IDs.
- The mean and standard deviation provide insights into the central tendency and dispersion of the category IDs, respectively.

It is important to note that the `.describe()` function primarily analyzes numerical data. Therefore, to thoroughly investigate the dataset, especially the non-numeric types like `catgroup`, `catname`, and `catdesc`, we will need to employ additional methods tailored for textual or categorical data analysis.

In [3]:
categories.describe()

catid
count  11.000000
mean    6.000000
std     3.316625
min     1.000000
25%     3.500000
50%     6.000000
75%     8.500000
max    11.000000

**Dates**

The `dates` table holds information about possible dates when tickets were sold. The attributes captured here are as follows: 
- **dateid**: unique identifier
- **caldate**: the respective datetime object 
- **day**: the day of the week that particular date falls on, abrreviated by the first two letters of the day 
- **week**: indicates which week out of the year (1-53) the date falls on 
- **qtr**: indicates which quarter of the year the date falls on 
- **year**: indicates which year the date falls on 
- **holiday**: boolean value indicating whether or not the respective day was a holiday

The `dates` table allows for the analysis of trends in ticket sales in regards to time-related factors such as seasonality, month, and day of the week. Gaining a better understanding of when ticket sales increase or decrease can drive decision-making for marketing or sales teams. 

In [4]:
select * from public.date order by dateid

dateid                   caldate  day  week  month  qtr  year  holiday
0      1827 2008-01-01 00:00:00+00:00  WE      1  JAN      1  2008     True
1      1828 2008-01-02 00:00:00+00:00  TH      1  JAN      1  2008    False
2      1829 2008-01-03 00:00:00+00:00  FR      1  JAN      1  2008    False
3      1830 2008-01-04 00:00:00+00:00  SA      2  JAN      1  2008    False
4      1831 2008-01-05 00:00:00+00:00  SU      2  JAN      1  2008    False
..      ...                       ...  ...   ...    ...  ...   ...      ...
360    2187 2008-12-27 00:00:00+00:00  SA     53  DEC      4  2008    False
361    2188 2008-12-28 00:00:00+00:00  SU     53  DEC      4  2008    False
362    2189 2008-12-29 00:00:00+00:00  MO     53  DEC      4  2008    False
363    2190 2008-12-30 00:00:00+00:00  TU     53  DEC      4  2008    False
364    2191 2008-12-31 00:00:00+00:00  WE     53  DEC      4  2008    False

[365 rows x 8 columns]

The following is a brief overview of the dates dataset, using the `.describe()` method. The output gives us some key statistics of each column in the dataset, including the mean, max, and min values to see how data is distributed. This also allows us to catch some irregularities or missing values we need to address in the cleaning stage before analysis. 

Here are some key points we can see: 
- There are 365 rows or records in the table. 
- All dates were from the year 2008
- Date ids begin at 1827 and go through 2191

It is important to note that the describe function only analyzes numerical data, so in order to investigate data in non-numeric types, we will need to use another method. 

In [5]:
dates.describe()

dateid        week         qtr    year
count   365.000000  365.000000  365.000000   365.0
mean   2009.000000   27.145205    2.509589  2008.0
std     105.510663   15.080854    1.118300     0.0
min    1827.000000    1.000000    1.000000  2008.0
25%    1918.000000   14.000000    2.000000  2008.0
50%    2009.000000   27.000000    3.000000  2008.0
75%    2100.000000   40.000000    4.000000  2008.0
max    2191.000000   53.000000    4.000000  2008.0

On it's own, the dates dataset is not particularly useful, but we can join it to other tables where we want to know a bit more about the date attached to a record. The dateid is used as a foreign key in several of the tables we discuss here.

**Events**

The `events` table holds information about past events where tickets were sold. The attributes captured here are as follows: 
- **eventid**: unique identifier for each event.
- **venueid**: identifier for the venue where the event took place.
- **catid**: category identifier for the type of event.
- **dateid**: identifier linking to the date the event occurred.
- **eventname**: the name of the event.
- **starttime**: the start time of the event.

The `events` table allows for the analysis of trends in ticket sales in regards to the timing, location, and type of events. Gaining a better understanding of when ticket sales change can help in predicting future sales, optimizing event scheduling, and tailoring marketing strategies to target audiences more effectively. By analyzing this data, organizations can identify peak sales periods, popular venues, and preferred event categories, enabling them to make informed decisions that enhance customer satisfaction and maximize revenue.

In [6]:
select * from public.event order by eventid

eventid  venueid  ...                    eventname                 starttime
0           1      305  ...              Gotterdammerung 2008-01-25 14:30:00+00:00
1           2      306  ...                Boris Godunov 2008-10-15 20:00:00+00:00
2           3      302  ...                       Salome 2008-04-19 14:30:00+00:00
3           4      309  ...  La Cenerentola (Cinderella) 2008-09-21 14:30:00+00:00
4           5      302  ...                 Il Trovatore 2008-06-05 19:00:00+00:00
...       ...      ...  ...                          ...                       ...
8793     8794       37  ...               Greg Kihn Band 2008-04-22 14:00:00+00:00
8794     8795       64  ...              Smokey Robinson 2008-02-20 19:00:00+00:00
8795     8796       28  ...                   John Mayer 2008-05-01 14:00:00+00:00
8796     8797       96  ...                  Keith Urban 2008-09-13 14:00:00+00:00
8797     8798      128  ...               Lynyrd Skynyrd 2008-08-11 20:00:00+00:00

[8798 rows x 6 columns]

In the same fashion used to get an overview of the dates table, we can get some insight on all the tables used. Let's look at the events table. 

From the function output, we can see some key facts: 
- there are 8798 rows in the datset
- eventids and venueids range from 1 - 8798 
- catids range from 6 - 9 
- dateids range from 1827 to 2191 

The foreign keys can be joined to other tables to get more information. 

In [7]:
events.describe()

eventid      venueid        catid       dateid
count  8798.000000  8798.000000  8798.000000  8798.000000
mean   4399.500000   139.448852     8.045238  2007.344283
std    2539.908168    92.146241     1.176674   105.886050
min       1.000000     1.000000     6.000000  1827.000000
25%    2200.250000    58.000000     7.000000  1914.000000
50%    4399.500000   115.000000     9.000000  2007.000000
75%    6598.750000   225.000000     9.000000  2099.000000
max    8798.000000   309.000000     9.000000  2191.000000

Let's dive a little deeper into the text data. Starting with event name, we can pull a list of all the different events captured in this dataset using the .unique() function in Python.

Using SQL, we can run some testing queries to figure out which data needs some cleaning up before our analysis. I chose to run a count of null values for each attribute. They each returned 0 null values so I do not think there is any cleaning to do here just yet. Be advised, as we may discover different reasons to clean or transform the data later. 

In [8]:
# number of unique events
len(events['eventname'].unique())

576

In [9]:
select count(*) from public.event where starttime is null

count
0      0

**Listings**

The `listings` table holds information about past listings where tickets were for sale. The attributes captured here are as follows: 
- **listid**: unique identifier
- **sellerid**: identifier for the seller
- **eventid**: identifier for the event
- **dateid**: identifier for the date of the event
- **numtickets**: number of tickets listed
- **priceperticket**: price per individual ticket
- **totalprice**: total price for all tickets listed
- **listtime**: timestamp for when the listing was created

The `listings` table allows for the analysis of trends in ticket sales in regards to event popularity and seasonal variations. Gaining a better understanding of when ticket sales change can help in predicting future sales trends and in planning marketing strategies.

In [10]:
select * from public.listing order by listid

listid  sellerid  ...  totalprice                  listtime
0            1     36861  ...      1820.0 2008-01-24 06:43:29+00:00
1            2     16002  ...      1631.0 2008-03-05 12:25:29+00:00
2            3     21461  ...       364.0 2008-11-01 07:35:33+00:00
3            4      8117  ...       304.0 2008-05-24 01:18:37+00:00
4            5      1616  ...       700.0 2008-05-17 02:29:11+00:00
...        ...       ...  ...         ...                       ...
192492  235492     28329  ...       683.0 2008-08-25 01:16:59+00:00
192493  235493     18347  ...      1282.0 2008-01-06 03:51:51+00:00
192494  235494     23875  ...      1790.0 2008-06-20 01:50:24+00:00
192495  235496     24966  ...      8455.0 2008-07-10 04:49:44+00:00
192496  235497     34696  ...      5370.0 2008-08-18 07:40:04+00:00

[192497 rows x 8 columns]

Let's look at the listings table. 

Some key facts we can pull from the output: 
- there are 19,2497 rows in the datset
- sellerids range from 1 to 49990 (not every seller will be included in this dataset)
- eventids range from 1 to 8798 (there will be repeated events in this dataset)
- dateids range from 1827 to 2191, so all dates in the dates table are present here 
- the number of tickets sold in one listing ranges from 1 to 30, with an average of 10 tickets sold per listing
- the price per ticket ranges from $20 to $2500, so the average price of a ticket is about $397
- the total price of a listing ranges from $20 to $20,000 with an average total price of $3070 

The foreign keys can be joined to other tables to get more information. 

In [11]:
listings.describe()

listid       sellerid  ...  priceperticket     totalprice
count  192497.000000  192497.000000  ...   192497.000000  192497.000000
mean   108857.667995   24963.952804  ...      397.305849    3034.417913
std     66488.097591   14434.467776  ...      494.007844    3069.708939
min         1.000000       1.000000  ...       20.000000      20.000000
25%     52543.000000   12429.000000  ...      131.000000     822.000000
50%    105202.000000   25032.000000  ...      244.000000    2009.000000
75%    158773.000000   37486.000000  ...      408.000000    4228.000000
max    235497.000000   49990.000000  ...     2500.000000   20000.000000

[8 rows x 7 columns]

We can run some more testing queries to ensure our data makes sense. Here, we'd want to start by looking at numtickets, priceperticket, and totalprice, as values like 0 or negative numbers would not make sense. Everything is looking good here!

In [12]:
select count(*) from public.listing where totalprice = 0

count
0      0

**Sales**

The `sales` table holds information about past ticket sales. The attributes captured here are as follows: 
- **salesid**: unique identifier
- **listid**: foreign key from listings
- **sellerid**: unique identifier for the seller
- **buyerid**: unique identifier for the buyer
- **eventid**: foreign key from events 
- **dateid**: foreign key from dates
- **qtysold**: the number of tickets sold in the respective sale record
- **pricepaid**: the amount of money the tickets sold for
- **commission**: the amount of money made by commission for the respective sale record
- **saletime**: datetime object of the sale  

The `sales` table allows for the analysis of trends in ticket sales in regards to seasonal patterns, popular events, and buyer behavior. Gaining a better understanding of when ticket sales change can help in predicting future sales trends and in planning marketing strategies.

In [13]:
select * from public.sales order by salesid

salesid  listid  ...  commission                  saletime
0             1       1  ...      109.20 2008-02-18 02:36:48+00:00
1             2       4  ...       11.40 2008-06-06 05:00:16+00:00
2             3       5  ...       52.50 2008-06-06 08:26:17+00:00
3             4       5  ...       26.25 2008-06-09 08:38:52+00:00
4             5       6  ...       23.10 2008-08-31 09:17:02+00:00
...         ...     ...  ...         ...                       ...
172451   172452  235476  ...      226.35 2008-10-22 02:27:22+00:00
172452   172453  235479  ...      670.20 2008-08-30 02:27:23+00:00
172453   172454  235479  ...      335.10 2008-10-10 02:27:24+00:00
172454   172455  235482  ...      170.70 2008-12-03 02:27:26+00:00
172455   172456  235494  ...       53.70 2008-07-05 02:27:26+00:00

[172456 rows x 10 columns]

Some key facts about the sales table: 
- there are 172,456 sales recorded 
- listids range from 1 to 235494 so it is likely that multiple sales could be attached to the same listing
- sellerids, buyerids, eventids, and dateids will be repeated, allowing opportunity to group the data 
- the quantity of tickets in a sale ranges from 1 to 8, with an average of 2 tickets sold per sale
- the price paid by a buyer ranges from $20 to $12,624 per sale with an average of $642 per sale
- commission made by sellers ranges from $3 to $1,894 per sale with an average of $96

In [14]:
sales.describe()

salesid         listid  ...      pricepaid     commission
count  172456.000000  172456.000000  ...  172456.000000  172456.000000
mean    86228.500000  101476.463225  ...     642.282269      96.342340
std     49783.903349   62763.741083  ...     869.275106     130.391266
min         1.000000       1.000000  ...      20.000000       3.000000
25%     43114.750000   48411.000000  ...     194.000000      29.100000
50%     86228.500000   98445.000000  ...     386.000000      57.900000
75%    129342.250000  148334.500000  ...     758.000000     113.700000
max    172456.000000  235494.000000  ...   12624.000000    1893.600000

[8 rows x 9 columns]

Again, we can do some basic tests to confirm that all of our values are viable. Everything looks good here. 

In [15]:
select * from public.sales where commission <= 0

Empty DataFrame
Columns: [salesid, listid, sellerid, buyerid, eventid, dateid, qtysold, pricepaid, commission, saletime]
Index: []

**Users**

The `users` table holds information about users on the ticket platform. The attributes captured in this table are as follows:
- **userid**: unique identifier
- **username**: the unique username of each user
- **firstname**: the first name of each user
- **lastname**: the last name of each user 
- **city**: the city of each user
- **state**: the state in which each user resides
- **email**: email attached to the user
- **phone**: phone number attached to each user
- **likesports**, **liketheatre**, **likeconcerts**, **likejazz**, **likeclassical**, **likeopera**, **likerock**, **likevegas**, **likebroadway**, **likemusicals**: boolean indicators that detail user preferences

The `users` table allows for the analysis of trends in ticket sales in regards to users and their preferences. Gaining a better understanding of when ticket sales change can help in tailoring marketing strategies, identifying potential areas for growth, and enhancing user engagement by promoting events that align with their interests.

In [16]:
select * from public.users order by userid

userid  username   firstname  ... likevegas likebroadway likemusicals
0           1  JSG99FHE      Rafael  ...       1.0          0.0          1.0
1           2  PGL08LJI    Vladimir  ...       1.0          0.0          1.0
2           3  IFT66TXU        Lars  ...       NaN          NaN          1.0
3           4  XDZ38RDD       Barry  ...       NaN          NaN          0.0
4           5  AEB55QTM      Reagan  ...       1.0          0.0          1.0
...       ...       ...         ...  ...       ...          ...          ...
49985   49986  WSZ25RSI       Basil  ...       NaN          1.0          1.0
49986   49987  MMK88YWE      Lucian  ...       NaN          NaN          NaN
49987   49988  ERA75TVW      Hayden  ...       0.0          0.0          0.0
49988   49989  RRS41ZTJ  Evangeline  ...       NaN          0.0          1.0
49989   49990  ILI20QYV        Iola  ...       1.0          1.0          1.0

[49990 rows x 18 columns]

For the users table, we will not get much information out of running a describe() because nearly all of the values in the table are text or a boolean, represented as 0 or 1. 

Running it regardless, we can see: 
- there are 49990 users in this table 
- out of all of the users, we can see how many null values are left in each of the boolean categories that will need to be cleaned up, for example, there were only 17,454 valid records to the likesports attribute, so we can estimate that there are 32,536 null values in this area

In [17]:
users.describe()

userid    likesports  ...  likebroadway  likemusicals
count  49990.000000  17454.000000  ...  24928.000000  25107.000000
mean   24995.500000      0.497422  ...      0.496991      0.502131
std    14431.014315      0.500008  ...      0.500001      0.500005
min        1.000000      0.000000  ...      0.000000      0.000000
25%    12498.250000      0.000000  ...      0.000000      0.000000
50%    24995.500000      0.000000  ...      0.000000      1.000000
75%    37492.750000      1.000000  ...      1.000000      1.000000
max    49990.000000      1.000000  ...      1.000000      1.000000

[8 rows x 11 columns]

The users table is where data cleaning get's interesting! Since we have all these boolean indicators that have null values, we have to decide how we want to proceed. We can switch the values out or leave them but make subsets. 

If we switch the values out, we have to assume that a null value or a non-answer corresponds with a yes or no. For this table, we probably do not want to do that, as we would be assigning preferences to users and polluting our information with falsified values. 

In this case, splitting the data up by these values would give us a better picture of who likes what.

We can come back to these subsets later, as they can now also be joined with other tables.

In [18]:
sports_fans = users[users['likesports'] == 1]
sports_fans

userid  username firstname  ... likevegas likebroadway likemusicals
0           1  JSG99FHE    Rafael  ...       1.0          0.0          1.0
2           3  IFT66TXU      Lars  ...       NaN          NaN          1.0
8           9  MSD36KVR   Mufutau  ...       NaN          0.0          1.0
14         15  OWU78MTR  Scarlett  ...       NaN          1.0          NaN
31         32  BFR93AMT      Macy  ...       NaN          NaN          0.0
...       ...       ...       ...  ...       ...          ...          ...
49963   49964  ZDR14HNA    Palmer  ...       NaN          0.0          NaN
49965   49966  XXT27FBP    Hayden  ...       0.0          1.0          NaN
49982   49983  RCS76EGO  Colorado  ...       NaN          0.0          NaN
49983   49984  FFP96MVH     Caryn  ...       NaN          1.0          NaN
49985   49986  WSZ25RSI     Basil  ...       NaN          1.0          1.0

[8682 rows x 18 columns]

In [19]:
classical_fans = users[users['likeclassical'] == 1]
opera_fans = users[users['likeopera'] == 1]
rock_fans = users[users['likerock'] == 1]
vegas_fans = users[users['likevegas'] == 1]
broadway_fans = users[users['likebroadway'] == 1]
musicals_fans = users[users['likemusicals'] == 1]

**Venues**

The `venues` table holds information about venues on the ticket platform. The attributes captured in this table are as follows:
- **venueid**: unique identifier
- **venuename**: the name of each venue
- **venuecity**: the city of each venue
- **venuestate**: the state of each venue
- **email**: email attached to the user
- **venueseats**: the number of seats or capacity a venue has

The `venues` table allows for the analysis of trends in ticket sales in regards to venue. Gaining a better understanding of when ticket sales change based on the venue, city, state, or capacity size.

In [20]:
select * from public.venue order by venueid

venueid                  venuename      venuecity venuestate  venueseats
0          1                Toyota Park     Bridgeview         IL         0.0
1          2      Columbus Crew Stadium       Columbus         OH         0.0
2          3                RFK Stadium     Washington         DC         0.0
3          4  CommunityAmerica Ballpark    Kansas City         KS         0.0
4          5           Gillette Stadium     Foxborough         MA     68756.0
..       ...                        ...            ...        ...         ...
197      305          Lyric Opera House        Chicago         IL         0.0
198      306          Lyric Opera House      Baltimore         MD         0.0
199      307        San Francisco Opera  San Francisco         CA         0.0
200      308         Metropolitan Opera  New York City         NY         0.0
201      309          Los Angeles Opera    Los Angeles         CA         0.0

[202 rows x 5 columns]

Once again, the describe function is only going to show us a couple things as the venues table is mostly text. 

Here's what we can see: 
- there are 202 venues in this table 
- the capacity of a venue ranges from 0 to 91,704 people with an average of 17,504 

In [21]:
venues.describe()

venueid    venueseats
count  202.000000    187.000000
mean   131.252475  17503.962567
std     92.041309  27847.756840
min      1.000000      0.000000
25%     53.250000      0.000000
50%    104.500000      0.000000
75%    223.750000  41642.500000
max    309.000000  91704.000000

There is one glaring issue that we'd want to investigate first. There are 130 venues that have a value of 0 for venueseats. 

In some cases, you could reason why some venues wouldn't have seats, they could be outside or just set up as general admission. 

If 0 was a reasonable answer, we could keep it, but if we want a better idea of how venue capacity effects ticket sales, we need to find another way to correct these 0s. 

We could look up the capacity of each of these venues online and back fill using those estimates. That's assuming these venues are real and that information is publically or easily available. We have some other options as well. 

We could back fill with different averages: average over the entire dataset, average by state, or average by city. 

We could also get really fancy and pull down the average number of tickets sold for an event at that venue from our other tables. 

Let's try them all. 

In [22]:
venues[venues['venueseats'] == 0]

venueid                  venuename      venuecity venuestate  venueseats
0          1                Toyota Park     Bridgeview         IL         0.0
1          2      Columbus Crew Stadium       Columbus         OH         0.0
2          3                RFK Stadium     Washington         DC         0.0
3          4  CommunityAmerica Ballpark    Kansas City         KS         0.0
6          7                  BMO Field        Toronto         ON         0.0
..       ...                        ...            ...        ...         ...
197      305          Lyric Opera House        Chicago         IL         0.0
198      306          Lyric Opera House      Baltimore         MD         0.0
199      307        San Francisco Opera  San Francisco         CA         0.0
200      308         Metropolitan Opera  New York City         NY         0.0
201      309          Los Angeles Opera    Los Angeles         CA         0.0

[130 rows x 5 columns]

In [23]:
select venueid, venuename from public.venue where venueseats = 0 order by venuename

venueid                 venuename
0         39                ARCO Arena
1         44               AT&T Center
2         20         Air Canada Centre
3        200     Al Hirschfeld Theatre
4        201        Ambassador Theatre
..       ...                       ...
125       19           Wachovia Center
126      237       Walter Kerr Theatre
127      304  War Memorial Opera House
128      238     Winter Garden Theatre
129       61        Xcel Energy Center

[130 rows x 2 columns]

In [24]:
zero_venues = venues[venues['venueseats'] == 0]
zero_venues['venuename'].unique()

array(['Toyota Park', 'Columbus Crew Stadium', 'RFK Stadium',
       'CommunityAmerica Ballpark', 'BMO Field', 'The Home Depot Center',
       "Dick's Sporting Goods Park", 'Pizza Hut Park',
       'Robertson Stadium', 'Rice-Eccles Stadium', 'Buck Shaw Stadium',
       'TD Banknorth Garden', 'Izod Center', 'Wachovia Center',
       'Air Canada Centre', 'United Center', 'Quicken Loans Arena',
       'The Palace of Auburn Hills', 'Conseco Fieldhouse',
       'Bradley Center', 'Philips Arena', 'Time Warner Cable Arena',
       'American Airlines Arena', 'Amway Arena', 'Verizon Center',
       'Pepsi Center', 'Target Center', 'Ford Center', 'Rose Garden',
       'EnergySolutions Arena', 'Oracle Arena', 'Staples Center',
       'US Airways Center', 'ARCO Arena', 'American Airlines Center',
       'Toyota Center', 'FedExForum', 'New Orleans Arena', 'AT&T Center',
       'Prudential Center', 'Nassau Veterans Memorial Coliseum',
       'Mellon Arena', 'HSBC Arena', 'Bell Centre', 'Scotiabank P

Since there are 130 of them, I made a nice list above that I will try to feed into ChatGPT. It did pretty well and I filled out what I could find with my human brain. I do not recommend this method, but here you go. 

In [25]:
SELECT * FROM main.Sheet1

venueid                 venuename capacity
0         20         Air Canada Centre    19800
1        200     Al Hirschfeld Theatre   1424​​
2        201        Ambassador Theatre   1120​​
3         28   American Airlines Arena    19600
4         40  American Airlines Center    20000
..       ...                       ...      ...
104      236   Vivian Beaumont Theatre   1080​​
105       19           Wachovia Center    20478
106      237       Walter Kerr Theatre    945​​
107      238     Winter Garden Theatre     1526
108       61        Xcel Energy Center    18064

[109 rows x 3 columns]

In [26]:
venues_grouped = venues.groupby("venuecity")
venues_grouped.size()

venuecity
Anaheim         2
Arlington       1
Atlanta         3
Auburn Hills    1
Baltimore       3
               ..
Tampa           2
Toronto         3
Uniondale       1
Vancouver       1
Washington      4
Length: 79, dtype: int64

In [27]:
# make a copy of venues
avgcityvenues = venues.copy()

# Convert 'venueseats' to numeric, coercing errors to NaN (this will handle non-numeric values)
avgcityvenues['venueseats'] = pd.to_numeric(avgcityvenues['venueseats'], errors='coerce')

# Replace 0s with NaN
avgcityvenues['venueseats'].replace(0, np.nan, inplace=True)

# Calculate mean seats by city, excluding NaN values
city_means = avgcityvenues.groupby('venuecity')['venueseats'].mean()

# Map city means to each row in 'venues'. If 'venueseats' is NaN, replace it with the city's mean
avgcityvenues['venueseats'] = avgcityvenues.apply(
    lambda row: city_means[row['venuecity']] if pd.isnull(row['venueseats']) else row['venueseats'],
    axis=1
)

# Fill any remaining NaN values with 'Not Found'
avgcityvenues['venueseats'].fillna('Not Found', inplace=True)
avgcityvenues

venueid                  venuename      venuecity venuestate    venueseats
0          1                Toyota Park     Bridgeview         IL     Not Found
1          2      Columbus Crew Stadium       Columbus         OH     Not Found
2          3                RFK Stadium     Washington         DC       41888.0
3          4  CommunityAmerica Ballpark    Kansas City         KS       60122.0
4          5           Gillette Stadium     Foxborough         MA       68756.0
..       ...                        ...            ...        ...           ...
197      305          Lyric Opera House        Chicago         IL  48244.333333
198      306          Lyric Opera House      Baltimore         MD       59491.5
199      307        San Francisco Opera  San Francisco         CA       55673.0
200      308         Metropolitan Opera  New York City         NY       36162.5
201      309          Los Angeles Opera    Los Angeles         CA       56000.0

[202 rows x 5 columns]

In [28]:
avgcityvenues[avgcityvenues['venueseats'] == 'Not Found']

venueid                                venuename  ... venuestate venueseats
0          1                              Toyota Park  ...         IL  Not Found
1          2                    Columbus Crew Stadium  ...         OH  Not Found
7          8                    The Home Depot Center  ...         CA  Not Found
8          9               Dick's Sporting Goods Park  ...         CO  Not Found
9         10                           Pizza Hut Park  ...         TX  Not Found
11        13                      Rice-Eccles Stadium  ...         UT  Not Found
12        14                        Buck Shaw Stadium  ...         CA  Not Found
21        23               The Palace of Auburn Hills  ...         MI  Not Found
26        28                  American Airlines Arena  ...         FL  Not Found
27        29                              Amway Arena  ...         FL  Not Found
31        33                              Ford Center  ...         OK  Not Found
32        34                              Rose Garden  ...         OR  Not Found
33        35                    EnergySolutions Arena  ...         UT  Not Found
36        38                        US Airways Center  ...         AZ  Not Found
37        39                               ARCO Arena  ...         CA  Not Found
38        40                 American Airlines Center  ...         TX  Not Found
40        42                               FedExForum  ...         TN  Not Found
42        44                              AT&T Center  ...         TX  Not Found
43        45                        Prudential Center  ...         NJ  Not Found
44        46        Nassau Veterans Memorial Coliseum  ...         NY  Not Found
46        48                               HSBC Arena  ...         NY  Not Found
47        49                              Bell Centre  ...         QC  Not Found
48        50                         Scotiabank Place  ...         ON  Not Found
49        52                               RBC Center  ...         NC  Not Found
50        53                      BankAtlantic Center  ...         FL  Not Found
52        55                         Nationwide Arena  ...         OH  Not Found
56        59                     Pengrowth Saddledome  ...         AB  Not Found
57        60                             Rexall Place  ...         AB  Not Found
58        61                       Xcel Energy Center  ...         MN  Not Found
59        62                     General Motors Place  ...         BC  Not Found
61        65                         Jobing.com Arena  ...         AZ  Not Found
62        66                  HP Pavilion at San Jose  ...         CA  Not Found
88        92            University of Phoenix Stadium  ...         AZ  Not Found
113      117                              Chase Field  ...         AZ  Not Found
118      122  Saratoga Springs Performing Arts Center  ...         NY  Not Found
119      123                              Fox Theatre  ...         CA  Not Found
120      124                          Mountain Winery  ...         CA  Not Found
121      125                           Villa Montalvo  ...         CA  Not Found
123      127                    Superpages.com Center  ...         TX  Not Found
124      128                       E.J. Nutter Center  ...         OH  Not Found
125      129                      Hersheypark Stadium  ...         PA  Not Found
126      130                North Charleston Coliseum  ...         SC  Not Found
167      240               San Jose Repertory Theatre  ...         CA  Not Found
170      243                       Pasadena Playhouse  ...         CA  Not Found
177      250                             Sahara Hotel  ...         NV  Not Found
178      251                              Paris Hotel  ...         NV  Not Found
179      252                             Hilton Hotel  ...         NV  Not Found
180      253                             Mirage Hotel  ...         NV  Not Found
181      254                        

Averaging by city still left us with 60 venues with a "Not Found" capacity, so let's try averaging by state instead. 

In [29]:
# Make a copy of venues with the new name
avgstvenues = venues.copy()

# Convert 'venueseats' to numeric, coercing errors to NaN (this will handle non-numeric values)
avgstvenues['venueseats'] = pd.to_numeric(avgstvenues['venueseats'], errors='coerce')

# Replace 0s with NaN
avgstvenues['venueseats'].replace(0, np.nan, inplace=True)

# Calculate mean seats by state, excluding NaN values
state_means = avgstvenues.groupby('venuestate')['venueseats'].mean()

# Map state means to each row in 'avgstvenues'. If 'venueseats' is NaN, replace it with the state's mean
avgstvenues['venueseats'] = avgstvenues.apply(
    lambda row: state_means[row['venuestate']] if pd.isnull(row['venueseats']) else row['venueseats'],
    axis=1
)
avgstvenues

venueid                  venuename      venuecity venuestate    venueseats
0          1                Toyota Park     Bridgeview         IL  48244.333333
1          2      Columbus Crew Stadium       Columbus         OH  56034.750000
2          3                RFK Stadium     Washington         DC  41888.000000
3          4  CommunityAmerica Ballpark    Kansas City         KS           NaN
4          5           Gillette Stadium     Foxborough         MA  68756.000000
..       ...                        ...            ...        ...           ...
197      305          Lyric Opera House        Chicago         IL  48244.333333
198      306          Lyric Opera House      Baltimore         MD  70229.000000
199      307        San Francisco Opera  San Francisco         CA  51303.500000
200      308         Metropolitan Opera  New York City         NY  48764.000000
201      309          Los Angeles Opera    Los Angeles         CA  51303.500000

[202 rows x 5 columns]

Averaging by state still left us with 28 missing rows, but we can keep trying. Now let's get really janky here. 

In [109]:
import pandas as pd
import numpy as np

# Assuming 'venues' and 'venuecapacity' DataFrames are defined above this code block

# Joining the 'venues' table with the 'venuecapacity' table on 'venueid', while retaining only one 'venuename' column
venues_joined = venues.merge(venuecapacity[['venueid', 'capacity']], on='venueid', how='left')

# Convert 'capacity' to numeric, coercing errors to NaN (this will handle non-numeric values)
venues_joined['capacity'] = pd.to_numeric(venues_joined['capacity'], errors='coerce')

# Replace 0s with NaN in both 'venueseats' and 'capacity' to handle them uniformly
venues_joined['venueseats'].replace(0, np.nan, inplace=True)
venues_joined['capacity'].replace(0, np.nan, inplace=True)

# Filling null 'capacity' with 'venueseats' where applicable
venues_joined['capacity'] = venues_joined.apply(
    lambda row: row['venueseats'] if pd.isnull(row['capacity']) and not pd.isnull(row['venueseats']) else row['capacity'],
    axis=1
)

# Filling null 'venueseats' with 'capacity' where applicable
venues_joined['venueseats'] = venues_joined.apply(
    lambda row: row['capacity'] if pd.isnull(row['venueseats']) and not pd.isnull(row['capacity']) else row['venueseats'],
    axis=1
)

# Ensure 'venueseats' and 'capacity' are treated as numeric for comparison and aggregation
venues_joined['venueseats'] = pd.to_numeric(venues_joined['venueseats'], errors='coerce')
venues_joined['capacity'] = pd.to_numeric(venues_joined['capacity'], errors='coerce')

# Calculate average 'venueseats' by 'venuecity', excluding NaN values
city_means = venues_joined.groupby('venuecity')['venueseats'].mean()

# Calculate average 'capacity' by 'venuecity', excluding NaN values
city_capacity_means = venues_joined.groupby('venuecity')['capacity'].mean()

# When 'venueseats' is NaN, fill with the average by 'venuecity'
venues_joined['venueseats'] = venues_joined.apply(
    lambda row: city_means.get(row['venuecity'], np.nan) if pd.isnull(row['venueseats']) else row['venueseats'],
    axis=1
)

# When 'capacity' is NaN, fill with the average by 'venuecity'
venues_joined['capacity'] = venues_joined.apply(
    lambda row: city_capacity_means.get(row['venuecity'], np.nan) if pd.isnull(row['capacity']) else row['capacity'],
    axis=1
)

# Ensure there are no null or 0 values in 'venueseats' and 'capacity' by setting a default value if all else fails
default_value = 1
venues_joined['venueseats'].fillna(default_value, inplace=True)
venues_joined['venueseats'].replace(0, default_value, inplace=True)
venues_joined['capacity'].fillna(default_value, inplace=True)
venues_joined['capacity'].replace(0, default_value, inplace=True)

venues_joined

venueid                  venuename  ...    venueseats      capacity
0          1                Toyota Park  ...  20000.000000  20000.000000
1          2      Columbus Crew Stadium  ...  20011.000000  20011.000000
2          3                RFK Stadium  ...  45596.000000  45596.000000
3          4  CommunityAmerica Ballpark  ...   6537.000000   6537.000000
4          5           Gillette Stadium  ...  68756.000000  68756.000000
..       ...                        ...  ...           ...           ...
197      305          Lyric Opera House  ...  41412.500000  41412.500000
198      306          Lyric Opera House  ...  59491.500000  59491.500000
199      307        San Francisco Opera  ...  55673.000000  55673.000000
200      308         Metropolitan Opera  ...  19725.833333  19725.833333
201      309          Los Angeles Opera  ...  38000.000000  38000.000000

[202 rows x 6 columns]

In [110]:
venues_joined[venues_joined['venueseats'] == 1]

venueid                  venuename  ... venueseats capacity
119      123                Fox Theatre  ...        1.0      1.0
124      128         E.J. Nutter Center  ...        1.0      1.0
125      129        Hersheypark Stadium  ...        1.0      1.0
126      130  North Charleston Coliseum  ...        1.0      1.0
170      243         Pasadena Playhouse  ...        1.0      1.0
177      250               Sahara Hotel  ...        1.0      1.0
178      251                Paris Hotel  ...        1.0      1.0
179      252               Hilton Hotel  ...        1.0      1.0
180      253               Mirage Hotel  ...        1.0      1.0
181      254             Caesars Palace  ...        1.0      1.0
182      255             Venetian Hotel  ...        1.0      1.0
183      256            Paris MGM Grand  ...        1.0      1.0
184      257                Luxor Hotel  ...        1.0      1.0
185      258            Tropicana Hotel  ...        1.0      1.0
186      259              Harrahs Hotel  ...        1.0      1.0
187      260               Ballys Hotel  ...        1.0      1.0
188      261                 Wynn Hotel  ...        1.0      1.0
189      262         Mandalay Bay Hotel  ...        1.0      1.0
190      263             Bellagio Hotel  ...        1.0      1.0
191      264          New York New York  ...        1.0      1.0
195      303     Grand 1894 Opera House  ...        1.0      1.0

[21 rows x 6 columns]

In [116]:
venues_joined_updated = venues_joined.merge(avgstvenues[['venuestate', 'venueseats']], on='venuestate', how='left', suffixes=('', '_from_avgstvenues'))
venues_joined_updated['venueseats'] = venues_joined_updated['venueseats_from_avgstvenues']
venues_joined_updated['capacity'] = venues_joined_updated['venueseats_from_avgstvenues']
venues_joined_updated.drop(columns=['venueseats_from_avgstvenues'], inplace=True)
venues_joined_updated_grouped = venues_joined_updated.groupby('venueid').first().reset_index()
venues_joined_updated_grouped

venueid                  venuename  ...    venueseats      capacity
0          1                Toyota Park  ...  48244.333333  48244.333333
1          2      Columbus Crew Stadium  ...  56034.750000  56034.750000
2          3                RFK Stadium  ...  41888.000000  41888.000000
3          4  CommunityAmerica Ballpark  ...           NaN           NaN
4          5           Gillette Stadium  ...  68756.000000  68756.000000
..       ...                        ...  ...           ...           ...
197      305          Lyric Opera House  ...  48244.333333  48244.333333
198      306          Lyric Opera House  ...  70107.000000  70107.000000
199      307        San Francisco Opera  ...  51303.500000  51303.500000
200      308         Metropolitan Opera  ...  20000.000000  20000.000000
201      309          Los Angeles Opera  ...  51303.500000  51303.500000

[202 rows x 6 columns]

In [131]:
subset_joined_with_venuecapacity = subset.merge(venuecapacity, on='venuename', how='left')
subset_joined_with_venuecapacity

venueid_x                      venuename  ... venueid_y capacity_y
0           4      CommunityAmerica Ballpark  ...       4.0       6537
1          13            Rice-Eccles Stadium  ...      13.0      45807
2          33                    Ford Center  ...      33.0      18203
3          34                    Rose Garden  ...      34.0      19393
4          35          EnergySolutions Arena  ...      35.0      18306
5          38              US Airways Center  ...      38.0      18422
6          49                    Bell Centre  ...      49.0      21302
7          59           Pengrowth Saddledome  ...      59.0      19289
8          60                   Rexall Place  ...      60.0      18500
9          62           General Motors Place  ...      62.0      18910
10         65               Jobing.com Arena  ...      65.0      17125
11         92  University of Phoenix Stadium  ...      92.0      63400
12        117                    Chase Field  ...     117.0      48519
13        130      North Charleston Coliseum  ...     130.0    13295​​
14        250                   Sahara Hotel  ...       NaN        NaN
15        251                    Paris Hotel  ...       NaN        NaN
16        252                   Hilton Hotel  ...       NaN        NaN
17        253                   Mirage Hotel  ...       NaN        NaN
18        254                 Caesars Palace  ...       NaN        NaN
19        255                 Venetian Hotel  ...       NaN        NaN
20        256                Paris MGM Grand  ...       NaN        NaN
21        257                    Luxor Hotel  ...       NaN        NaN
22        258                Tropicana Hotel  ...       NaN        NaN
23        259                  Harrahs Hotel  ...       NaN        NaN
24        260                   Ballys Hotel  ...       NaN        NaN
25        261                     Wynn Hotel  ...       NaN        NaN
26        262             Mandalay Bay Hotel  ...       NaN        NaN
27        263                 Bellagio Hotel  ...       NaN        NaN
28        264              New York New York  ...       NaN        NaN

[29 rows x 8 columns]

We know that Vegas is just not ready to cooperate here, but that's okay. This is always a lesson in overdoing something, overanalyzing here leads to some anomalies and data loss. I cannot recommend it.

## Experimental Analysis

Now that we've got a good idea of what our data is looking like, we can come up some questions we want to answer. As our datasets are related to ticket sales, I'd like to see how different factors effect ticket sales. 

Let's look at: 
- How do dates effect ticket sales? Does day of the week, time of year, or holidays impact sales?
- Which events sold the most tickets over the year? 
- Which venues sold the most tickets over the year? Is there any impact on sales due to venue?
- Is there a connection between buyers, sellers, and ticket sales? 
- Are some sellers more likely to make a sale? 
- Are some buyers more likely to buy tickets from certain sellers? 
- As a seller increases in sales, do their listing prices change? 
- Which factors impact ticket sales the most?

### How do dates effect ticket sales?

Starting off, I want to analyze sales data so I am using the metrics of number of sales, number of listenings, and the sum of quanty sold. Then, we will be grouping the data based on the factors we are investigating for correlation. 

Below, I grouped the data based on day of the week. You can toggle the graph options to see how our metrics are effected by day of the week. I did not see any major differences in sales based on the day of the week alone. This is easy to spot using the graph, but we can confirm this with statistical methods if we wanted. 

In [135]:
select 
d.day,
count(salesid) as num_sales, 
count(listid) as num_listings, 
sum(qtysold) as total_tickets_sold 
from public.sales s
left join public.date d on s.dateid = d.dateid
group by d.day

day  num_sales  num_listings  total_tickets_sold
0  WE       24831         24831               49542
1  TH       24539         24539               49342
2  FR       24650         24650               49197
3  SA       24299         24299               48514
4  MO       24677         24677               49480
5  TU       24621         24621               49345
6  SU       24839         24839               49929

Next, I looked at how sales were affected based on if it was a holiday or not. This is a very striking and obvious correlation that says tickets sell better on non-holidays. 

In [140]:
select 
d.holiday,
count(salesid) as num_sales, 
count(listid) as num_listings, 
sum(qtysold) as total_tickets_sold 
from public.sales s
left join public.date d on s.dateid = d.dateid
group by d.holiday

holiday  num_sales  num_listings  total_tickets_sold
0     True       2297          2297                4581
1    False     170159        170159              340768

Let's check out quarter, month, and week. We will not be using year as we confirmed in the exploratory analysis that this dataset only spans over one year. 

In [141]:
select 
d.qtr,
count(salesid) as num_sales, 
count(listid) as num_listings, 
sum(qtysold) as total_tickets_sold 
from public.sales s
left join public.date d on s.dateid = d.dateid
group by d.qtr

qtr  num_sales  num_listings  total_tickets_sold
0    2      47243         47243               94479
1    3      48949         48949               98075
2    1      38203         38203               76674
3    4      38061         38061               76121

Now it's getting a little more interesting. 

We have a nice and almost normal distribution going on here, but we can see that quarter 2 and quarter three generate more sales than quarter 1 or quarter 2. 

Diving into weeks and months may help us rationalize why those quarters are performing better than others. 

In [142]:
select 
d.week,
count(salesid) as num_sales, 
count(listid) as num_listings, 
sum(qtysold) as total_tickets_sold 
from public.sales s
left join public.date d on s.dateid = d.dateid
group by d.week

week  num_sales  num_listings  total_tickets_sold
0      2        883           883                1746
1      4       2248          2248                4517
2      5       2786          2786                5663
3      7       3529          3529                7135
4      9       3857          3857                7642
5     10       3656          3656                7291
6     15       3549          3549                7054
7     16       3598          3598                7221
8     18       3638          3638                7348
9     19       3661          3661                7361
10    22       3611          3611                7197
11    23       3604          3604                7100
12    24       3712          3712                7463
13    25       3727          3727                7390
14    27       3691          3691                7362
15    28       3627          3627                7228
16    29       3638          3638                7305
17    33       3735          3735                7457
18    35       3701          3701                7345
19    37       3785          3785                7663
20    38       3714          3714                7610
21    39       3697          3697                7287
22    40       3825          3825                7684
23    42       3819          3819                7625
24    44       3224          3224                6471
25    46       3530          3530                6964
26    47       3236          3236                6478
27    52       1010          1010                2006
28     1         85            85                 170
29     3       1572          1572                3210
30     6       3111          3111                6174
31     8       3794          3794                7577
32    11       3822          3822                7531
33    12       3642          3642                7413
34    13       3678          3678                7506
35    14       3682          3682                7331
36    17       3474          3474                7029
37    20       3668          3668                7314
38    21       3673          3673                7366
39    26       3625          3625                7317
40    30       3800          3800                7690
41    31       3792          3792                7569
42    32       3701          3701                7537
43    34       3731          3731                7350
44    36       3678          3678                7335
45    41       3779          3779                7593
46    43       3791          3791                7582
47    45       4194          4194                8390
48    48       3025          3025                6033
49    49       2667          2667                5363
50    50       2308          2308                4625
51    51       1598          1598                3155
52    53        275           275                 576

Looking at week, we can see some major outliers, showing that the beginning and end of the calendar year produce less sales. This makes sense as those are holiday seasons in the US. We could also blame the weather if some events are outside or if some venues are just closed for the season. 

We can also see it peak at week 45, which is one of the first weeks of November. I would guess that this may be the time when people are purchasing tickets as gifts for the holidays or when there are holiday events going on that may generate more sales than usual.

In [144]:
select 
d.month,
count(salesid) as num_sales, 
count(listid) as num_listings, 
sum(qtysold) as total_tickets_sold 
from public.sales s
left join public.date d on s.dateid = d.dateid
group by d.month

month  num_sales  num_listings  total_tickets_sold
0   MAR        16338         16338               32840
1   APR        15374         15374               30827
2   JUL        16455         16455               33011
3   SEP        16060         16060               32240
4   NOV        14261         14261               28397
5   DEC         7059          7059               14144
6   JAN         7574          7574               15306
7   FEB        14291         14291               28528
8   MAY        16139         16139               32291
9   JUN        15730         15730               31361
10  AUG        16434         16434               32824
11  OCT        16741         16741               33580

The month chart really echoes what we were seeing before in the quarter chart. We see sales plummet in December and January, with high sales in summer and fall. 

From this evidence alone, we can say that are there are dead months that impact sales a lot. If we wanted to increase sales during those months, I could suggest a heavy marketing plan combined with discounts on tickets or on larger quantity orders to have people consider buying tickets for a later date as a present. 

### How do events effect ticket sales? 

In [37]:
select 
e.eventid,
e.eventname,
count(salesid) as num_sales, 
count(listid) as num_listings, 
sum(qtysold) as total_tickets_sold 
from public.sales s
left join public.event e on s.eventid = e.eventid
group by e.eventid, e.eventname

eventid           eventname  num_sales  num_listings  total_tickets_sold
0        8762               Oasis          8             8                  17
1        6605       David Sanborn         20            20                  45
2        2557  The Cherry Orchard          2             2                   6
3        5465             Journey         20            20                  44
4        2046            Our Town          7             7                  14
...       ...                 ...        ...           ...                 ...
8507     6783          The Police          8             8                  17
8508     5917          The Police         29            29                  68
8509     3331  Young Frankenstein         13            13                  26
8510     8415        Neil Diamond         14            14                  29
8511      540          Mamma Mia!          8             8                  19

[8512 rows x 5 columns]

From what we can see is that the number of events is far too large for us to get much out of this analysis. Instead, we can look at the categories table instead. As the categories and sales table do not share any attributes to join on, we can pull in the events table as a middle man. 

In [41]:
select 
c.catgroup, 
count(s.salesid) as num_sales, 
count(s.listid) as num_listings, 
sum(s.qtysold) as total_tickets_sold
from public.category c 
left join public.event e on c.catid = e.catid
left join public.sales s on e.eventid = s.eventid
group by c.catgroup

catgroup  num_sales  num_listings  total_tickets_sold
0    Sports          0             0                 NaN
1  Concerts      97582         97582            195444.0
2     Shows      74874         74874            149905.0

In [44]:
select 
c.catgroup, 
c.catid,
count(e.eventid) as num_events
from public.category c 
left join public.event e on c.catid = e.catid
group by c.catid, c.catgroup

catgroup  catid  num_events
0      Shows      6        1300
1      Shows      8         500
2     Sports      1           0
3   Concerts     11           0
4     Sports      3           0
5   Concerts      9        4998
6      Shows      7        2000
7     Sports      2           0
8   Concerts     10           0
9     Sports      4           0
10    Sports      5           0

We can see here though that events in the concerts category are more common and sell more tickets.

### How do buyers and sellers effect ticket sales?

In [47]:
select 
sellerid, 
sum(qtysold) as num_tickets_sold, 
count(listid) as num_listings, 
count(distinct(buyerid)) as num_unique_buyers
from public.sales 
group by sellerid
order by num_tickets_sold desc
limit 100


sellerid  num_tickets_sold  num_listings  num_unique_buyers
0         48950                46            19                 19
1         20029                41            15                 15
2         19123                41            16                 16
3         36791                40            17                 17
4         41579                39            18                 18
...         ...               ...           ...                ...
43430     12081                 1             1                  1
43431     24516                 1             1                  1
43432     34503                 1             1                  1
43433     19704                 1             1                  1
43434      3403                 1             1                  1

[43435 rows x 4 columns]

### How do venues effect ticket sales?